# Gecoding using OneMap API

- In this notebook, we will extract the latitude and longtitude coordinates using [OneMap API](https://www.onemap.gov.sg/docs/#introduction) developed by Singapre Land Transport Authority (LTA).

- The dataset is obtained from data.gov.sg and contains the [HDB resale flat prices](https://data.gov.sg/dataset/resale-flat-prices) from Jan 2019 to Sep 2022.

- Reference: [Geocoding Singapore Coordinates: OneMap API](https://towardsdatascience.com/geocoding-singapore-coordinates-onemap-api-3e1542bf26f7)

## Import Python Modules

In [1]:
import json
import requests
import pandas as pd

## Read Dataset

In [2]:
df = pd.read_csv('resale-flat-prices-based-on-registration-date-from-jan-2019-onwards.csv')

In [3]:
df.head()

month        town flat_type block        street_name storey_range  \
0  2019-01  ANG MO KIO    3 ROOM   225   ANG MO KIO AVE 1     01 TO 03   
1  2019-01  ANG MO KIO    3 ROOM   174   ANG MO KIO AVE 4     01 TO 03   
2  2019-01  ANG MO KIO    3 ROOM   440  ANG MO KIO AVE 10     04 TO 06   
3  2019-01  ANG MO KIO    3 ROOM   174   ANG MO KIO AVE 4     10 TO 12   
4  2019-01  ANG MO KIO    3 ROOM   637   ANG MO KIO AVE 6     01 TO 03   

   floor_area_sqm      flat_model  lease_commence_date     remaining_lease  \
0            67.0  New Generation                 1978            58 years   
1            60.0        Improved                 1986            66 years   
2            67.0  New Generation                 1979            59 years   
3            61.0        Improved                 1986   66 years 01 month   
4            68.0  New Generation                 1980  60 years 08 months   

   resale_price  
0      230000.0  
1      235000.0  
2      238000.0  
3      240000.0  
4      240000.0

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 93611 entries, 0 to 93610
Data columns (total 11 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   month                93611 non-null  object 
 1   town                 93611 non-null  object 
 2   flat_type            93611 non-null  object 
 3   block                93611 non-null  object 
 4   street_name          93611 non-null  object 
 5   storey_range         93611 non-null  object 
 6   floor_area_sqm       93611 non-null  float64
 7   flat_model           93611 non-null  object 
 8   lease_commence_date  93611 non-null  int64  
 9   remaining_lease      93611 non-null  object 
 10  resale_price         93611 non-null  float64
dtypes: float64(2), int64(1), object(8)
memory usage: 7.9+ MB


In [5]:
# Create a column for address to combine the block and street name
df['address'] = df['block'] + " " + df['street_name']
address_list = list(df['address'])

In [6]:
address_list

['225 ANG MO KIO AVE 1',
 '174 ANG MO KIO AVE 4',
 '440 ANG MO KIO AVE 10',
 '174 ANG MO KIO AVE 4',
 '637 ANG MO KIO AVE 6',
 '571 ANG MO KIO AVE 3',
 '505 ANG MO KIO AVE 8',
 '631 ANG MO KIO AVE 4',
 '440 ANG MO KIO AVE 10',
 '474 ANG MO KIO AVE 10',
 '403 ANG MO KIO AVE 10',
 '445 ANG MO KIO AVE 10',
 '557 ANG MO KIO AVE 10',
 '585 ANG MO KIO AVE 3',
 '107 ANG MO KIO AVE 4',
 '333 ANG MO KIO AVE 1',
 '631 ANG MO KIO AVE 4',
 '108 ANG MO KIO AVE 4',
 '564 ANG MO KIO AVE 3',
 '225 ANG MO KIO AVE 1',
 '330 ANG MO KIO AVE 1',
 '473 ANG MO KIO AVE 10',
 '121 ANG MO KIO AVE 3',
 '421 ANG MO KIO AVE 10',
 '606 ANG MO KIO AVE 5',
 '211 ANG MO KIO AVE 3',
 '121 ANG MO KIO AVE 3',
 '417 ANG MO KIO AVE 10',
 '345 ANG MO KIO AVE 3',
 '557 ANG MO KIO AVE 10',
 '215 ANG MO KIO AVE 1',
 '345 ANG MO KIO AVE 3',
 '649 ANG MO KIO AVE 5',
 '513 ANG MO KIO AVE 8',
 '418 ANG MO KIO AVE 10',
 '421 ANG MO KIO AVE 10',
 '507 ANG MO KIO AVE 8',
 '465 ANG MO KIO AVE 10',
 '643 ANG MO KIO AVE 5',
 '524 ANG MO

## Obtain Coordinates using OneMap API

In [7]:
# Function to obtain the Latitude and Longitude using OneMap API
def getcoordinates(address):
    req = requests.get('https://developers.onemap.sg/commonapi/search?searchVal='+address+'&returnGeom=Y&getAddrDetails=Y&pageNum=1')
    resultsdict = eval(req.text)
    if len(resultsdict['results'])>0:
        return resultsdict['results'][0]['LATITUDE'], resultsdict['results'][0]['LONGITUDE']
    else:
        pass

In [8]:
# Loop each address in the address list
coordinateslist= []
count = 0
failed_count = 0
for address in address_list:
    try:
        if len(getcoordinates(address))>0:
            count = count + 1
            print('Extracting',count,'out of',len(address_list),'addresses')
            coordinateslist.append(getcoordinates(address))
    except:
        count = count + 1           
        failed_count = failed_count + 1
        print('Failed to extract',count,'out of',len(address_list),'addresses')
        coordinateslist.append(None)
print('Total Number of Addresses With No Coordinates',failed_count)

Extracting 1 out of 93611 addresses
Extracting 2 out of 93611 addresses
Extracting 3 out of 93611 addresses
Extracting 4 out of 93611 addresses
Extracting 5 out of 93611 addresses
Extracting 6 out of 93611 addresses
Extracting 7 out of 93611 addresses
Extracting 8 out of 93611 addresses
Extracting 9 out of 93611 addresses
Extracting 10 out of 93611 addresses
Extracting 11 out of 93611 addresses
Extracting 12 out of 93611 addresses
Extracting 13 out of 93611 addresses
Extracting 14 out of 93611 addresses
Extracting 15 out of 93611 addresses
Extracting 16 out of 93611 addresses
Extracting 17 out of 93611 addresses
Extracting 18 out of 93611 addresses
Extracting 19 out of 93611 addresses
Extracting 20 out of 93611 addresses
Extracting 21 out of 93611 addresses
Extracting 22 out of 93611 addresses
Extracting 23 out of 93611 addresses
Extracting 24 out of 93611 addresses
Extracting 25 out of 93611 addresses
Extracting 26 out of 93611 addresses
Extracting 27 out of 93611 addresses
Extracting

Extracting 221 out of 93611 addresses
Extracting 222 out of 93611 addresses
Extracting 223 out of 93611 addresses
Extracting 224 out of 93611 addresses
Extracting 225 out of 93611 addresses
Extracting 226 out of 93611 addresses
Extracting 227 out of 93611 addresses
Extracting 228 out of 93611 addresses
Extracting 229 out of 93611 addresses
Extracting 230 out of 93611 addresses
Extracting 231 out of 93611 addresses
Extracting 232 out of 93611 addresses
Extracting 233 out of 93611 addresses
Extracting 234 out of 93611 addresses
Extracting 235 out of 93611 addresses
Extracting 236 out of 93611 addresses
Extracting 237 out of 93611 addresses
Extracting 238 out of 93611 addresses
Extracting 239 out of 93611 addresses
Extracting 240 out of 93611 addresses
Extracting 241 out of 93611 addresses
Extracting 242 out of 93611 addresses
Extracting 243 out of 93611 addresses
Extracting 244 out of 93611 addresses
Extracting 245 out of 93611 addresses
Extracting 246 out of 93611 addresses
Extracting 2

Extracting 438 out of 93611 addresses
Extracting 439 out of 93611 addresses
Extracting 440 out of 93611 addresses
Extracting 441 out of 93611 addresses
Extracting 442 out of 93611 addresses
Extracting 443 out of 93611 addresses
Extracting 444 out of 93611 addresses
Extracting 445 out of 93611 addresses
Extracting 446 out of 93611 addresses
Extracting 447 out of 93611 addresses
Extracting 448 out of 93611 addresses
Extracting 449 out of 93611 addresses
Extracting 450 out of 93611 addresses
Extracting 451 out of 93611 addresses
Extracting 452 out of 93611 addresses
Extracting 453 out of 93611 addresses
Extracting 454 out of 93611 addresses
Extracting 455 out of 93611 addresses
Extracting 456 out of 93611 addresses
Extracting 457 out of 93611 addresses
Extracting 458 out of 93611 addresses
Extracting 459 out of 93611 addresses
Extracting 460 out of 93611 addresses
Extracting 461 out of 93611 addresses
Extracting 462 out of 93611 addresses
Extracting 463 out of 93611 addresses
Extracting 4

Extracting 654 out of 93611 addresses
Extracting 655 out of 93611 addresses
Extracting 656 out of 93611 addresses
Extracting 657 out of 93611 addresses
Extracting 658 out of 93611 addresses
Extracting 659 out of 93611 addresses
Extracting 660 out of 93611 addresses
Extracting 661 out of 93611 addresses
Extracting 662 out of 93611 addresses
Extracting 663 out of 93611 addresses
Extracting 664 out of 93611 addresses
Extracting 665 out of 93611 addresses
Extracting 666 out of 93611 addresses
Extracting 667 out of 93611 addresses
Extracting 668 out of 93611 addresses
Extracting 669 out of 93611 addresses
Extracting 670 out of 93611 addresses
Extracting 671 out of 93611 addresses
Extracting 672 out of 93611 addresses
Extracting 673 out of 93611 addresses
Extracting 674 out of 93611 addresses
Extracting 675 out of 93611 addresses
Extracting 676 out of 93611 addresses
Extracting 677 out of 93611 addresses
Extracting 678 out of 93611 addresses
Extracting 679 out of 93611 addresses
Extracting 6

Extracting 871 out of 93611 addresses
Extracting 872 out of 93611 addresses
Extracting 873 out of 93611 addresses
Extracting 874 out of 93611 addresses
Extracting 875 out of 93611 addresses
Extracting 876 out of 93611 addresses
Extracting 877 out of 93611 addresses
Extracting 878 out of 93611 addresses
Extracting 879 out of 93611 addresses
Extracting 880 out of 93611 addresses
Extracting 881 out of 93611 addresses
Extracting 882 out of 93611 addresses
Extracting 883 out of 93611 addresses
Extracting 884 out of 93611 addresses
Extracting 885 out of 93611 addresses
Extracting 886 out of 93611 addresses
Extracting 887 out of 93611 addresses
Extracting 888 out of 93611 addresses
Extracting 889 out of 93611 addresses
Extracting 890 out of 93611 addresses
Extracting 891 out of 93611 addresses
Extracting 892 out of 93611 addresses
Extracting 893 out of 93611 addresses
Extracting 894 out of 93611 addresses
Extracting 895 out of 93611 addresses
Extracting 896 out of 93611 addresses
Extracting 8

...

Extracting 92744 out of 93611 addresses
Extracting 92745 out of 93611 addresses
Extracting 92746 out of 93611 addresses
Extracting 92747 out of 93611 addresses
Extracting 92748 out of 93611 addresses
Extracting 92749 out of 93611 addresses
Extracting 92750 out of 93611 addresses
Extracting 92751 out of 93611 addresses
Extracting 92752 out of 93611 addresses
Extracting 92753 out of 93611 addresses
Extracting 92754 out of 93611 addresses
Extracting 92755 out of 93611 addresses
Extracting 92756 out of 93611 addresses
Extracting 92757 out of 93611 addresses
Extracting 92758 out of 93611 addresses
Extracting 92759 out of 93611 addresses
Extracting 92760 out of 93611 addresses
Extracting 92761 out of 93611 addresses
Extracting 92762 out of 93611 addresses
Extracting 92763 out of 93611 addresses
Extracting 92764 out of 93611 addresses
Extracting 92765 out of 93611 addresses
Extracting 92766 out of 93611 addresses
Extracting 92767 out of 93611 addresses
Extracting 92768 out of 93611 addresses


Extracting 92950 out of 93611 addresses
Extracting 92951 out of 93611 addresses
Extracting 92952 out of 93611 addresses
Extracting 92953 out of 93611 addresses
Extracting 92954 out of 93611 addresses
Extracting 92955 out of 93611 addresses
Extracting 92956 out of 93611 addresses
Extracting 92957 out of 93611 addresses
Extracting 92958 out of 93611 addresses
Extracting 92959 out of 93611 addresses
Extracting 92960 out of 93611 addresses
Extracting 92961 out of 93611 addresses
Extracting 92962 out of 93611 addresses
Extracting 92963 out of 93611 addresses
Extracting 92964 out of 93611 addresses
Extracting 92965 out of 93611 addresses
Extracting 92966 out of 93611 addresses
Extracting 92967 out of 93611 addresses
Extracting 92968 out of 93611 addresses
Extracting 92969 out of 93611 addresses
Extracting 92970 out of 93611 addresses
Extracting 92971 out of 93611 addresses
Extracting 92972 out of 93611 addresses
Extracting 92973 out of 93611 addresses
Extracting 92974 out of 93611 addresses


Extracting 93156 out of 93611 addresses
Extracting 93157 out of 93611 addresses
Extracting 93158 out of 93611 addresses
Extracting 93159 out of 93611 addresses
Extracting 93160 out of 93611 addresses
Extracting 93161 out of 93611 addresses
Extracting 93162 out of 93611 addresses
Extracting 93163 out of 93611 addresses
Extracting 93164 out of 93611 addresses
Extracting 93165 out of 93611 addresses
Extracting 93166 out of 93611 addresses
Extracting 93167 out of 93611 addresses
Extracting 93168 out of 93611 addresses
Extracting 93169 out of 93611 addresses
Extracting 93170 out of 93611 addresses
Extracting 93171 out of 93611 addresses
Extracting 93172 out of 93611 addresses
Extracting 93173 out of 93611 addresses
Extracting 93174 out of 93611 addresses
Extracting 93175 out of 93611 addresses
Extracting 93176 out of 93611 addresses
Extracting 93177 out of 93611 addresses
Extracting 93178 out of 93611 addresses
Extracting 93179 out of 93611 addresses
Extracting 93180 out of 93611 addresses


Extracting 93361 out of 93611 addresses
Extracting 93362 out of 93611 addresses
Extracting 93363 out of 93611 addresses
Extracting 93364 out of 93611 addresses
Extracting 93365 out of 93611 addresses
Extracting 93366 out of 93611 addresses
Extracting 93367 out of 93611 addresses
Extracting 93368 out of 93611 addresses
Extracting 93369 out of 93611 addresses
Extracting 93370 out of 93611 addresses
Extracting 93371 out of 93611 addresses
Extracting 93372 out of 93611 addresses
Extracting 93373 out of 93611 addresses
Extracting 93374 out of 93611 addresses
Extracting 93375 out of 93611 addresses
Extracting 93376 out of 93611 addresses
Extracting 93377 out of 93611 addresses
Extracting 93378 out of 93611 addresses
Extracting 93379 out of 93611 addresses
Extracting 93380 out of 93611 addresses
Extracting 93381 out of 93611 addresses
Extracting 93382 out of 93611 addresses
Extracting 93383 out of 93611 addresses
Extracting 93384 out of 93611 addresses
Extracting 93385 out of 93611 addresses


Extracting 93566 out of 93611 addresses
Extracting 93567 out of 93611 addresses
Extracting 93568 out of 93611 addresses
Extracting 93569 out of 93611 addresses
Extracting 93570 out of 93611 addresses
Extracting 93571 out of 93611 addresses
Extracting 93572 out of 93611 addresses
Extracting 93573 out of 93611 addresses
Extracting 93574 out of 93611 addresses
Extracting 93575 out of 93611 addresses
Extracting 93576 out of 93611 addresses
Extracting 93577 out of 93611 addresses
Extracting 93578 out of 93611 addresses
Extracting 93579 out of 93611 addresses
Extracting 93580 out of 93611 addresses
Extracting 93581 out of 93611 addresses
Extracting 93582 out of 93611 addresses
Extracting 93583 out of 93611 addresses
Extracting 93584 out of 93611 addresses
Extracting 93585 out of 93611 addresses
Extracting 93586 out of 93611 addresses
Extracting 93587 out of 93611 addresses
Extracting 93588 out of 93611 addresses
Extracting 93589 out of 93611 addresses
Extracting 93590 out of 93611 addresses


In [9]:
# Create the coordinates dataframe and join it with df
df_coordinates = pd.DataFrame(coordinateslist)
df_combined = df.join(df_coordinates)
df_combined = df_combined.rename(columns={0:'Latitude', 1:'Longitude'}) 

In [10]:
df_combined.head()

month        town flat_type block        street_name storey_range  \
0  2019-01  ANG MO KIO    3 ROOM   225   ANG MO KIO AVE 1     01 TO 03   
1  2019-01  ANG MO KIO    3 ROOM   174   ANG MO KIO AVE 4     01 TO 03   
2  2019-01  ANG MO KIO    3 ROOM   440  ANG MO KIO AVE 10     04 TO 06   
3  2019-01  ANG MO KIO    3 ROOM   174   ANG MO KIO AVE 4     10 TO 12   
4  2019-01  ANG MO KIO    3 ROOM   637   ANG MO KIO AVE 6     01 TO 03   

   floor_area_sqm      flat_model  lease_commence_date     remaining_lease  \
0            67.0  New Generation                 1978            58 years   
1            60.0        Improved                 1986            66 years   
2            67.0  New Generation                 1979            59 years   
3            61.0        Improved                 1986   66 years 01 month   
4            68.0  New Generation                 1980  60 years 08 months   

   resale_price                address          Latitude         Longitude  
0      230000.0   225 ANG MO KIO AVE 1  1.36739612776859  103.838150007464  
1      235000.0   174 ANG MO KIO AVE 4  1.37509746867904   103.83761896123  
2      238000.0  440 ANG MO KIO AVE 10  1.36642789831215  103.854311491141  
3      240000.0   174 ANG MO KIO AVE 4  1.37509746867904   103.83761896123  
4      240000.0   637 ANG MO KIO AVE 6  1.38036187235317  103.842334616577

## Save the dataset

In [11]:
df_combined.to_csv('hdb_resale_price_with coordinates.csv',index=False)